#### Dependencies

In [1]:
# System dependencies
from os import listdir
import time as clock
from IPython.display import clear_output

In [2]:
import pickle
import gzip
import re

In [3]:
# Data manipulation dependencies
import pandas as pd
import numpy as np
import datetime as dt

In [4]:
# Directory to save to
save_dir = '../data/continued/'

# Directory of prev job scans
id_dir = '../data/labels/IDs/'

In [5]:
# Directory of recent saved comet jobs
source_dir = '/oasis/projects/nsf/sys200/stats/xsede_stats/'

In [6]:
chosen = ('34583358', 'comet-15-11', '2020-07-08T18:25:03')

In [7]:
contents = listdir(source_dir)
contents

['archive_of_archive',
 'gordon_hostfile_logs',
 'gordon_pickles',
 'comet_accounting',
 'gordon_accounting',
 'comet_pickles',
 'archive',
 '.htaccess',
 'comet_hostfile_logs']

In [8]:
possible = [ source_dir+file_name for file_name in listdir(source_dir) ]

for item in possible:
    try:
        listdir(item)
    except:
        print(item)

/oasis/projects/nsf/sys200/stats/xsede_stats/gordon_hostfile_logs
/oasis/projects/nsf/sys200/stats/xsede_stats/gordon_pickles
/oasis/projects/nsf/sys200/stats/xsede_stats/gordon_accounting
/oasis/projects/nsf/sys200/stats/xsede_stats/comet_pickles
/oasis/projects/nsf/sys200/stats/xsede_stats/.htaccess
/oasis/projects/nsf/sys200/stats/xsede_stats/comet_hostfile_logs


In [9]:
locs = { 'aofa': source_dir+'archive_of_archive',
         'job_info': source_dir+'comet_accounting',
         'arc': source_dir+'archive'
         #'host_info': source_dir+'comet_hostfile_logs',
         #'old_pickles': source_dir+'comet_pickles'
       }

In [10]:
for key,loc in locs.items():
    print(loc)

/oasis/projects/nsf/sys200/stats/xsede_stats/archive_of_archive
/oasis/projects/nsf/sys200/stats/xsede_stats/comet_accounting
/oasis/projects/nsf/sys200/stats/xsede_stats/archive


## Prep Cleaning

In [63]:
def get_time( spec=None ):
    if type(spec) is str:
        spec = float( spec )
    
    return clock.strftime("%Y-%m-%dT%H:%M:%S", clock.localtime( spec ))

In [71]:
def get_stamp( spec ):
    sf = "%Y-%m-%dT%H:%M:%S"
    return int(clock.mktime( clock.strptime( spec, sf ) ))

In [12]:
def check_header( line ):
    if line.find(" ") < 0:
        try:
            return line[0] == '%'
        except:
            return False
        
    else:
        chunks = line.split(" ")
        try:
            return (chunks[0][0] == '%') or ( chunks[2].find("comet") >= 0 )
        except:
            return False

In [13]:
def check_job( chunk ):
    return chunk.find("-") == -1

In [14]:
def open_txt( txt_file ):
    
    with open( txt_file, "rt" ) as f:
        lines = f.readlines()
        f.close()
    
    return lines

In [15]:
def unzip_txt( gzipped ):
    
    with gzip.open( gzipped, 'rt') as f:
        lines = f.readlines()
        f.close()
    
    return lines

In [16]:
def quick_save( obj, label=get_time() ):
    
    try:
        out_file = open( label, 'wb')
        pickle.dump( obj, out_file)
        
        # double check save
        check_cpicore_set = pickle.load(open(cpiset_out, 'rb'))
        check_cpicore_set = None
        
    except:
        "There was a problem pickling the object - Save manually."

In [17]:
def info_dict( rules, info ):
    rules_list = rules.split("|")
    
    if len(rules_list) != len(info):
        return {}
    
    else:
        return { rules_list[i]:info[i] for i in range(len(rules_list)) }

In [18]:
def host_to_info_dict( zip_txt ):
    contents = unzip_txt( zip_txt )
    host_name = contents[1].partition(" ")[2][:11]
    out_dict = { host_name: {} }
    host_info = {}
    info_dict = { "Data":{},
                    "Job":"N/A",
                    "Schemas":{},
                    "Specs":[]
                }
    
    for line in contents:
            
        if line[0] == "$":
            info_dict["Specs"].append( format_spec( line ) )
            
        elif line[0] == "!":
            info_dict["Schemas"].update( format_schema( line ) )
        
        else:
            
            if (len(line) > 0) and (len(line) < 3 or check_header( line )):
                header_dict = format_header( line )
                
                if header_dict:
                    t = header_dict["Timestamp"]
                    host_info[ t ] = {}
                    
                    if check_job( header_dict["Jobid"] ):
                        info_dict["Job"] = { "Jobid": header_dict["Jobid"] } 
                    
            else:
                incoming = format_data( line )
                info_dict["Data"].update(incoming)
                
                host_info[t].update( info_dict )
                
    out_dict[host_name].update( host_info )
    
    return out_dict

In [19]:
def job_to_info_dict( txt_file_list ):
    nodes_by_date = {}
    unsaved = []

    for date in txt_file_list:
        try:
            # skip alt files
            #check_stamp = int( date[-14] )
            
            # read in file contents
            contents = open_txt( date )
            
            # formatting
            label = date[-14:-4]
            rules = contents[0]
            jobs = contents[1:]
            
            # template to save
            nodes_by_date[ label ] = {}
            nodes_by_date[ label ]["multiple"] = {}
            nodes_by_date[ label ]["rules"] = rules
            
            # run through lines in file
            for job in jobs:
                line = job.split("|")
                node = line[-1]
                info = info_dict( rules, line )
                
                # save multiple node jobs to specified loc
                if len(node) > 12:                
                    nodes_by_date[ label ][ "multiple" ][ node ] = info
                
                else:
                    nodes_by_date[ label ][ node[:11] ] = info
        except:
            unsaved.append(date)
            
    
    return nodes_by_date, unsaved

In [20]:
def format_header( line ):
    chunks = line.split(" ")
    
    try:
        if chunks[0][0] == '%':
            return {}
        else:
            return { "Timestamp": get_time( chunks[0] ), 
                     "Jobid": chunks[1],
                     "Host": chunks[2][:11] }
        
    except:
        return {}

In [21]:
def format_spec( line ):
    return line[1:-1]

In [22]:
def format_schema( line ):
    chunks = line.partition(" ")
    
    stat = chunks[0][1:]
    schemas = chunks[2:]
    
    return { stat:schemas }

In [23]:
def format_data( line ):
    chunks = line.split(" ")
    
    stat = chunks[0]
    dev = chunks[1]
    data = chunks[2:-1]
    
    return { (stat,dev): data }

### Parse file in archive

In [24]:
arc_data = [ locs['arc']+'/'+host_dir+'/'+stamp 
            for host_dir in listdir(locs['arc'])
            for stamp in listdir(locs['arc']+'/'+host_dir)  ]

aofa_data = [ locs['aofa']+'/'+host_dir+'/'+stamp 
            for host_dir in listdir(locs['aofa'])
            for stamp in listdir(locs['aofa']+'/'+host_dir)  ]

In [25]:
for f in arc_data:
    if chosen[1] in f:
        print(f)

/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1587865291.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1593654104.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1575315654.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1587951691.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1591753299.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1594258904.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1586482888.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1591062096.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1588556492.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1589420494.gz
/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1596418907.gz
/oasis/projects/nsf/sys200/stats

In [26]:
len(arc_data)

270054

In [28]:
group = [arc_data[0], arc_data[798], arc_data[23], arc_data[399], arc_data[25178] ]
for temp_loc in group:
    print(temp_loc)
    print()

/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-10-14.sdsc.edu/1587951665.gz

/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-12-13.sdsc.edu/1588340250.gz

/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-10-14.sdsc.edu/1594258873.gz

/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-16-12.sdsc.edu/1593135701.gz

/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-03-27.sdsc.edu/1586310014.gz



In [29]:
test_group = {}

for temp_loc in group:
    test_group.update( host_to_info_dict( temp_loc ) )

In [30]:
hosts = list(test_group.keys())
hosts

['comet-10-14', 'comet-12-13', 'comet-16-12', 'comet-03-27']

In [31]:
h1 = hosts[0]
h1_times = list(test_group[ h1 ].keys())
t1 = h1_times[0]
h1_t1 = test_group[ h1 ][ t1 ]
h1_t1

{'Data': {('block', 'md0'): ['3769',
   '0',
   '191372',
   '0',
   '3891',
   '0',
   '124',
   '0',
   '0',
   '0'],
  ('block', 'md1'): ['999325',
   '0',
   '68156122',
   '0',
   '28917805',
   '0',
   '1158146056',
   '0',
   '0',
   '0'],
  ('block', 'sda'): ['890112',
   '5472',
   '83697119',
   '1081384',
   '117486703',
   '5937063',
   '16317649323',
   '200119151',
   '0',
   '42811693'],
  ('block', 'sdb'): ['879909',
   '5472',
   '83830051',
   '1032785',
   '113539585',
   '5571314',
   '16176321227',
   '208213983',
   '0',
   '42896718'],
  ('cpu', '22'): ['482249526', '819', '10625141', '552844745', '1312314', '0'],
  ('cpu', '20'): ['515625092', '1068', '11812965', '518746297', '855428', '0'],
  ('cpu', '21'): ['520545061',
   '1578',
   '11355117',
   '513825177',
   '1381534',
   '0'],
  ('cpu', '11'): ['654967499', '245', '11514124', '378940446', '1784408', '0'],
  ('cpu', '10'): ['642735081', '362', '12240739', '390712771', '1439984', '0'],
  ('cpu', '13'): ['

## Summarize test cases

In [32]:
test_cases = []

for host,t_dict in test_group.items():
    for t in t_dict.keys():
        if type(test_group[ host ][ t ]['Job']) is dict:
            jobid = test_group[ host ][ t ]['Job']['Jobid']
            test_cases.append( (host,jobid,t) )

In [33]:
test_jobs = {}

for case in test_cases:
    host = case[0]
    jobid = case[1]
    date = case[2]
    
    if (host,jobid) not in test_jobs.keys():
        test_jobs[ (host,jobid) ] = date

In [34]:
test_cases

[('comet-10-14', '34592830', '2020/07/09 02:25:39'),
 ('comet-10-14', '34592831', '2020/07/09 02:25:40'),
 ('comet-10-14', '34592832', '2020/07/09 02:25:41'),
 ('comet-10-14', '34592833', '2020/07/09 02:25:42'),
 ('comet-10-14', '34592834', '2020/07/09 02:25:44'),
 ('comet-10-14', '34592837', '2020/07/09 02:25:45'),
 ('comet-10-14', '34592835', '2020/07/09 02:25:46'),
 ('comet-10-14', '34592836', '2020/07/09 02:25:47'),
 ('comet-10-14', '34592836', '2020/07/09 02:35:47'),
 ('comet-10-14', '34592836', '2020/07/09 02:45:47'),
 ('comet-10-14', '34592836', '2020/07/09 02:55:48'),
 ('comet-10-14', '34592836', '2020/07/09 03:05:48'),
 ('comet-10-14', '34592836', '2020/07/09 03:15:48'),
 ('comet-10-14', '34592836', '2020/07/09 03:25:48'),
 ('comet-10-14', '34592836', '2020/07/09 03:35:48'),
 ('comet-10-14', '34592836', '2020/07/09 03:45:49'),
 ('comet-10-14', '34592836', '2020/07/09 03:55:49'),
 ('comet-10-14', '34592836', '2020/07/09 04:05:49'),
 ('comet-10-14', '34592836', '2020/07/09 04:15

# Parse file in comet_accounting

In [36]:
acct_info_locs = [ locs['job_info']+'/'+stamp for stamp in listdir(locs['job_info']) ]
acct_list = [ loc[-14:-4] for loc in acct_info_locs ]

In [40]:
for job_tup,t in test_jobs.items():
    if t[:10] in acct_list:
        print("Found:", job_tup, t)
    else:
        print("Not Found:", job_tup, t)

Not Found: ('comet-10-14', '34592830') 2020/07/09 02:25:39
Not Found: ('comet-10-14', '34592831') 2020/07/09 02:25:40
Not Found: ('comet-10-14', '34592832') 2020/07/09 02:25:41
Not Found: ('comet-10-14', '34592833') 2020/07/09 02:25:42
Not Found: ('comet-10-14', '34592834') 2020/07/09 02:25:44
Not Found: ('comet-10-14', '34592837') 2020/07/09 02:25:45
Not Found: ('comet-10-14', '34592835') 2020/07/09 02:25:46
Not Found: ('comet-10-14', '34592836') 2020/07/09 02:25:47
Not Found: ('comet-10-14', '34597180') 2020/07/09 07:14:36
Not Found: ('comet-10-14', '34597688') 2020/07/09 09:45:04
Not Found: ('comet-10-14', '34597689') 2020/07/09 09:45:05
Not Found: ('comet-10-14', '34597694') 2020/07/09 09:45:06
Not Found: ('comet-10-14', '34597690') 2020/07/09 09:45:07
Not Found: ('comet-10-14', '34597692') 2020/07/09 09:45:08
Not Found: ('comet-10-14', '34597693') 2020/07/09 09:45:09
Not Found: ('comet-10-14', '34597695') 2020/07/09 09:45:10
Not Found: ('comet-10-14', '34602180') 2020/07/09 13:35:

In [41]:
temp = acct_info_locs[0]
temp

'/oasis/projects/nsf/sys200/stats/xsede_stats/comet_accounting/2019-09-19.txt'

In [42]:
job_sample = open_txt( temp )

In [43]:
rules = job_sample[0]
rules.split("|")

['JobID',
 'User',
 'Account',
 'Start',
 'End',
 'Submit',
 'Partition',
 'Timelimit',
 'JobName',
 'State',
 'NNodes',
 'ReqCPUS',
 'NodeList\n']

In [44]:
job_sample[1].split("|")

['26617639',
 'cipres',
 'sds121',
 '2019-09-12T05:12:16',
 '2019-09-19T05:12:30',
 '2019-09-12T05:12:10',
 'shared',
 '7-00:00:00',
 'NGBW-JOB-MRBAYES_XSEDE-1AA1022FA22D445DAB262C7D61CB6616',
 'TIMEOUT',
 '1',
 '16',
 'comet-04-40\n']

In [45]:
job_sample[1:]

['26617639|cipres|sds121|2019-09-12T05:12:16|2019-09-19T05:12:30|2019-09-12T05:12:10|shared|7-00:00:00|NGBW-JOB-MRBAYES_XSEDE-1AA1022FA22D445DAB262C7D61CB6616|TIMEOUT|1|16|comet-04-40\n',
 '26618425|cipres|sds121|2019-09-12T06:27:21|2019-09-19T06:27:28|2019-09-12T06:27:21|compute|7-00:00:00|NGBW-JOB-JMODELTEST2_XSEDE-A7B81541E1DF42F5A332ED19BE47DAE2|TIMEOUT|1|24|comet-17-48\n',
 '26618465|cipres|sds121|2019-09-12T06:28:54|2019-09-19T06:28:59|2019-09-12T06:28:51|compute|7-00:00:00|NGBW-JOB-JMODELTEST2_XSEDE-32AF6F93F6AB4ADAA6FC62855CC9B261|TIMEOUT|1|24|comet-27-64\n',
 '26619940|cipres|sds121|2019-09-12T09:06:06|2019-09-19T09:06:36|2019-09-12T09:06:03|compute|7-00:00:00|NGBW-JOB-GPHOCS_XSEDE-23CCC6C010CD4526B4514144918E7145|TIMEOUT|1|24|comet-04-69\n',
 '26694681|jwestern|cit121|2019-09-18T23:29:00|2019-09-19T23:28:26|2019-09-14T16:42:50|compute|23:59:00|rp12e07g2C0.17|TIMEOUT|16|384|comet-14-[37-38,42-44,56-57,59-60,62-64,66-69]\n',
 '26697694|cipres|sds121|2019-09-14T21:18:44|2019-09-

In [46]:
nodes_dict,not_found = job_to_info_dict( acct_info_locs )

In [47]:
nodes_dict['2019-09-19']

{'multiple': {'comet-14-[37-38,42-44,56-57,59-60,62-64,66-69]\n': {'JobID': '26694681',
   'User': 'jwestern',
   'Account': 'cit121',
   'Start': '2019-09-18T23:29:00',
   'End': '2019-09-19T23:28:26',
   'Submit': '2019-09-14T16:42:50',
   'Partition': 'compute',
   'Timelimit': '23:59:00',
   'JobName': 'rp12e07g2C0.17',
   'State': 'TIMEOUT',
   'NNodes': '16',
   'ReqCPUS': '384',
   'NodeList\n': 'comet-14-[37-38,42-44,56-57,59-60,62-64,66-69]\n'},
  'comet-14-[10,17,21,23,26,32,36,40],comet-16-[08,11-16,18,26-32,49,69],comet-27-[19-20,31-32,39,42,44,48-49,56-57,63,66-68]\n': {'JobID': '26745059',
   'User': 'liwenfei',
   'Account': 'cla174',
   'Start': '2019-09-17T18:48:24',
   'End': '2019-09-19T10:56:19',
   'Submit': '2019-09-16T22:22:22',
   'Partition': 'compute',
   'Timelimit': '2-00:00:00',
   'JobName': 'batch_script',
   'State': 'COMPLETED',
   'NNodes': '40',
   'ReqCPUS': '960',
   'NodeList\n': 'comet-14-[10,17,21,23,26,32,36,40],comet-16-[08,11-16,18,26-32,49,69

# Target job

In [48]:
chosen

('34583358', 'comet-15-11', '2020-07-08T18:25:03')

In [96]:
jobid = chosen[0]
host = chosen[1]
start = chosen[2]
start

'2020-07-08T18:25:03'

In [90]:
start_stamp = get_stamp( start )
start_stamp

1594257903

In [81]:
collected = []

for title in arc_data:
    if host in title:
        collected.append( title )
        
for title in aofa_data:
    if host in title:
        collected.append( title )

In [94]:
ts_file = []

for title in collected:
    try:
        ts = get_time( title[-13:-3] )
        if '2020-07-08' in ts:
            ts_file.append(title)
            
    except:
        next
ts_file

['/oasis/projects/nsf/sys200/stats/xsede_stats/archive/comet-15-11.sdsc.edu/1594258904.gz']

In [103]:
host_data = host_to_info_dict( ts_file[0] )
host_data

{'comet-15-11': {'2020-07-08T18:41:44': {'Data': {('block', 'md0'): ['14726',
     '0',
     '751024',
     '0',
     '411',
     '0',
     '124',
     '0',
     '0',
     '0'],
    ('block', 'md1'): ['3084294',
     '0',
     '112957202',
     '0',
     '16065162',
     '0',
     '317795920',
     '0',
     '0',
     '0'],
    ('block', 'sda'): ['1518710',
     '32511',
     '61419931',
     '1020512',
     '19113861',
     '3434264',
     '2644845403',
     '40940208',
     '0',
     '7262955'],
    ('block', 'sdb'): ['1495028',
     '32401',
     '56634643',
     '975278',
     '17500221',
     '3290116',
     '2638754635',
     '49060939',
     '0',
     '7312102'],
    ('cpu', '22'): ['810146542',
     '347',
     '11158530',
     '222949142',
     '2050939',
     '0'],
    ('cpu', '20'): ['835990948',
     '435',
     '11688929',
     '196628956',
     '2088221',
     '0'],
    ('cpu', '21'): ['828357965',
     '708',
     '11262830',
     '204706209',
     '2074631',
     '0'],


In [92]:
date = chosen[2][:10]
job = ''
for loc in acct_info_locs:
    if date in loc:
        job = loc
job

'/oasis/projects/nsf/sys200/stats/xsede_stats/comet_accounting/2020-07-08.txt'

In [100]:
jobid

'34583358'

In [98]:
chosen_sample = open_txt(job)

for line in chosen_sample:
    if jobid in line:
        print(line)

In [99]:
chosen_sample

['JobID|User|Account|Start|End|Submit|Partition|Timelimit|JobName|State|NNodes|ReqCPUS|NodeList\n',
 '33863705|gpalermo|csd650|2020-07-07T21:31:11|2020-07-08T19:44:35|2020-06-03T03:42:09|compute|1-00:00:00|ass_36|FAILED|2|48|comet-16-[12,26]\n',
 '34364605|amcisaac|mit178|2020-07-06T03:08:41|2020-07-08T03:08:46|2020-06-29T08:40:42|compute|2-00:00:00|cs_8A11A_ctr6_opt_14|TIMEOUT|1|24|comet-05-32\n',
 '34365157|amcisaac|mit178|2020-07-06T03:08:41|2020-07-08T03:08:46|2020-06-29T08:48:41|compute|2-00:00:00|cs_9A12A_ctr3_opt_10|TIMEOUT|1|20|comet-12-04\n',
 '34394408|cipres|sds121|2020-07-01T01:16:42|2020-07-08T01:16:54|2020-07-01T01:16:38|shared|7-00:00:00|NGBW-JOB-MRBAYES_XSEDE-B2C0A4CD0AE54D7A8A2BED531C56983F|TIMEOUT|1|8|comet-10-03\n',
 '34394419|cipres|sds121|2020-07-01T01:18:21|2020-07-08T01:18:25|2020-07-01T01:18:14|shared|7-00:00:00|NGBW-JOB-MRBAYES_XSEDE-AFD9CAD454CB4CDE966658ED5CB56305|TIMEOUT|1|8|comet-10-02\n',
 '34394434|cipres|sds121|2020-07-01T01:21:39|2020-07-08T01:21:55|202